# Remapping the Initial Dataset
---


This notebook serves as a template for the interpolation of initial data onto the limited area grid.  
The interpolation is performed by the `Climate Data Operators (CDO)`. 

The **CDO (Climate Data Operators)** are a collection of command-line operators to manipulate and analyze NetCDF and GRIB data. The CDO package is developed and maintained at the MPI for Meteorology in Hamburg. The CDO are also capable of remapping data to regular grids and triangular grids. Here, we will demonstrate how the CDO command-line tools can be used for the interpolation of the initial datasets.

## Preparations

Internally, the CDOs make use of the ECCodes package for GRIB2 decoding/encoding:

In [ ]:
module load eccodes
export ECCODES_DEFINITION_PATH=/pool/data/ICON/ICON_training/eccodes/definitions.edzw-2.27.0-1:$ECCODES_DEFINITION_PATH

We need to specify the input and output grid:

In [ ]:
export INGRID="/scratch/${USER::1}/$USER/example_data/const/icon_grid_0026_R03B07_G.nc"  # grid for which the input data has been provided
export LOCALGRID="/pool/data/ICON/ICON_training/exercise_lam/grids/iconR3B08_DOM01.nc"   # this is the name (and path) of the destination grid (limited area grid)

The following command defines the output directory as well as the filename containing the remapped data:

In [ ]:
# Create directory where the pre-processed input (initial and boundary data) for the LAM run is stored
export DATADIR_LAM=/scratch/${USER::1}/$USER/data_lam
mkdir -p ${DATADIR_LAM}
export OUTFILE="$DATADIR_LAM/init_ML_20210714T000000Z.nc"

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Define the absolute path of the raw initial data set from the example raw data set that has been discussed in <a href="../icon_exercise_prepare_lam.ipynb">icon_exercise_prepare_lam.ipynb</a>.
</div>

In [ ]:
export DATAFILE=???

<details>
<summary style="font-size: 1.1em;">Solution</summary>

`export DATAFILE="/scratch/${USER::1}/$USER/example_data/raw_data/init_ML_20210714T000000Z.grb"`

</details>

Specify the `FIELDS` to be remapped. See table 11.3 in the tutorial for further information.

In [ ]:
export FIELDS=ALB_SEAICE,C_T_LK,EVAP_PL,FR_ICE,FRESHSNW,H_ICE,H_ML_LK,H_SNOW,P,QC,QI,QR,QS,QV,QV_S,RHO_SNOW,SMI,T,T_BOT_LK,T_G,T_ICE,T_MNW_LK,T_SNOW,T_SO,T_WML_LK,U,V,W,W_I,W_SNOW,W_SO_ICE,Z0,HHL

## Identify the correct grid

Technically, the ICON grid files contain sub-grids, namely cells (triangles), edges and vertices. For the remapping with `CDO`, we need to select the correct grid number in the netCDF grid definition file in order to generate the interpolation weights.

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Inspect the input data grid file <code>INGRID</code> and the data file <code>DATAFILE</code>. Which grid number <code>IGN</code> in the grid file corresponds to the horizontal grid of the variables listed in <code>FIELDS</code>?
</div>

In [ ]:
IGN=???

<details>
<summary style="font-size: 1.1em;">Solution</summary>

`module load cdo`
`cdo sinfov $DATAFILE`

The number of the vertical grid is displayed in the 7th column, the horizontal grid in the ninth column of the output:
```
    -1 : Institut Source   T Steptype Levels Num    Points Num Dtype : Parameter name
     1 : DWD      unknown  v instant       1   1   2949120   1  P16  : FR_LAND       
     2 : DWD      unknown  v instant       1   1   2949120   1  P16  : QV_S          
     3 : DWD      unknown  v instant       1   1   2949120   1  P16  : T_G           
     4 : DWD      unknown  v instant       1   1   2949120   1  P16  : W_I    
```

For the variables in `FIELDS`, it is thus the following grid:
```
     1 : unstructured             : points=2949120
                             grid : number=26  position=1
                             uuid : a27b8de6-18c4-11e4-820a-b5b098c6a5c0
```

Now this grid needs to be identified in the input grid file:

`cdo sinfov $INGRID`

The corresponding grid with `2949120` points has number 1 in `INGRID`:

```
     1 : unstructured             : points=2949120  nvertex=3
                             grid : number=26  position=0
                              uri : http://icon-downloads.mpimet.mpg.de/grids/public/icon_grid_0026_R03B07_G.nc
                             clon : -3.141593 to 3.141593 radian
                             clat : -1.56928 to 1.56928 radian
                        available : cellbounds
                             uuid : a27b8de6-18c4-11e4-820a-b5b098c6a5c0
```

`IGN=1`

Please note that grid number 1 is also the default for the `CDO` command that will be used in the following, so in this case, an explicit specification of the grid would not be necessary. This might be different in other grid files, though.

</details>


<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    At which position in the triangles are the corresponding coordinates located?
</div>

<details>
<summary style="font-size: 1.1em;">Solution</summary>

The dimensions `clon` and `clat` are the longitude/latitude values of the midpoints of triangle circumcircles (Section 2.1.1 of the tutorial).

</details>

<div class="alert alert-success">
    <b style="color:#2d4b9b;">Exercise:</b> 
    Now identify the corresponding grid number <code>TGN</code> in target grid file.
</div>

In [ ]:
TGN=???

### Solution

<details>
<summary style="font-size: 1.1em;">Solution</summary>

`module load cdo`
`cdo sinfov $LOCALGRID`

The grid with dimensions `clat` and `clon` has number 2:
```
     2 : unstructured             : points=37488  nvertex=3
                             grid : number=102  position=0
                             clon : 0.01426315 to 0.2926627 radian
                             clat : 0.7672772 to 1.005925 radian
                        available : cellbounds
                             uuid : 936f1ca2-6345-6e84-7704-52b7cb2c26a0
```

`TGN=2`

</details>

## Remapping

We  choose 1st order conservative remapping as a remapping method. Since the correct grid number of the input grid (`IGN`) and the target grid (`TGN`) have been identified, we can select these grids in the cdo command:

In [ ]:
module load cdo
cdo -f nc2 remapcon,$LOCALGRID:$TGN -selname,$FIELDS -setgrid,$INGRID:$IGN $DATAFILE $OUTFILE

**Notes:**
- We chose `NetCDF` as file format of the output file by specifying `-f nc2`. The filename `$OUTFILE` was specified accordingly.
- CDO allows also to precalculate remapping weights which can significantly speed up the interpolation in case of multiple files on identical grids.
- Further details on initial data remapping with CDO can be found in Section 2.2.3 of the tutorial.

---

## Further Reading and Resources

- **ICON Manual:** <a href="https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html">https://www.dwd.de/DE/leistungen/nwv_icon_tutorial/nwv_icon_tutorial.html</a>    <br/>A new <b>draft version</b> of the ICON Tutorial is available here: <a href="https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html">https://icon-training-2025-scripts-rendering-cc74a6.gitlab-pages.dkrz.de/index.html</a>. It is currently being finalized and will be published soon.
  - Grid file description
    - ICON Manual, Chapter 2
  - Necessary input data tables
    - ICON Manual, Chapter 11
  - Remapping initial data using CDO
    - ICON Manual, Section 2.2.2
- CDO code and documentation: https://code.mpimet.mpg.de/projects/cdo
- CDO usage examples (interpolation onto regular grids): https://www.dwd.de/DE/leistungen/opendata/help/modelle/Opendata_cdo_DE.pdf?__blob=publicationFile&v=4


---

*Author info: Deutscher Wetterdienst (DWD) 2025 ::  icon@dwd.de. For a full list of contributors, see CONTRIBUTING in the root directory. License info: see LICENSE file.*